In [1]:
# Colab runs Linux + Python 3.10, fully compatible with Pathway

!pip install -q pathway \
    langchain-google-genai \
    langchain-community \
    langchain-chroma \
    langchain-huggingface \
    sentence-transformers \
    pandas \
    rank_bm25 \
    python-dotenv


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.3/53.3 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.3/67.3 kB 4.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.9/70.9 MB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.3/66.3 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 26.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 777.6/777.6 kB 20.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.7/21.7 MB 32.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 26.5/26.5 MB 34.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 2.7 MB/s eta 0:0

In [2]:
import pathway as pw
import pandas as pd
import json
import io
import os


In [5]:
from google.colab import files

print("Upload your Google service account credentials.json")
uploaded = files.upload()

assert "credentials.json" in uploaded, "credentials.json not uploaded"
print("credentials.json uploaded successfully")


Upload your Google service account credentials.json


Saving credentials.json to credentials.json
credentials.json uploaded successfully


In [6]:
BOOKS_FOLDER_ID = "1aZUgJc387xlfkUpCr_qxYMd5ewX3miVs"
BACKSTORY_FOLDER_ID = "1Cfq3O-gHASl8OI4qIfBj_ko6t1PhPObE"


In [7]:
books_table = pw.io.gdrive.read(
    object_id=BOOKS_FOLDER_ID,
    service_user_credentials_file="credentials.json",
    mode="static",
    format="binary",
    with_metadata=True,
    file_name_pattern="*.txt"
)

books_df = pw.debug.table_to_pandas(
    books_table.select(
        file_name=pw.this._metadata["name"],
        data=pw.this.data
    )
)

books_df["content"] = books_df["data"].apply(
    lambda x: x.decode("utf-8", errors="ignore")
)

print(f"Loaded {len(books_df)} books")
books_df[["file_name", "content"]].head()


Loaded 2 books


file_name  \
^YD9T51JS0TQN1TSVWX9H1CX22M  ((("T")), (("h")), (("e")), ((" ")), (("C")), ...   
^3EEQF01F65HMV8J9KGAQDP7PQC  ((("I")), (("n")), ((" ")), (("s")), (("e")), ...   

                                                                       content  
^YD9T51JS0TQN1TSVWX9H1CX22M  ﻿The Project Gutenberg eBook of The Count of M...  
^3EEQF01F65HMV8J9KGAQDP7PQC  *** START OF THE PROJECT GUTENBERG EBOOK 46597...

In [9]:
for _, row in books_df.iterrows():
    file_name = str(row["file_name"])   # <-- FIX
    clean_name = file_name.replace('"', "").replace("'", "")
    with open(f"local_{clean_name}", "w", encoding="utf-8") as f:
        f.write(row["content"])

print("Saved all books as local_*.txt")



Saved all books as local_*.txt


In [10]:
backstory_table = pw.io.gdrive.read(
    object_id=BACKSTORY_FOLDER_ID,
    service_user_credentials_file="credentials.json",
    mode="static",
    format="binary",
    with_metadata=True,
    file_name_pattern="*.csv"
)

backstory_df = pw.debug.table_to_pandas(
    backstory_table.select(
        file_name=pw.this._metadata["name"],
        data=pw.this.data
    )
)

backstory_df["content"] = backstory_df["data"].apply(
    lambda x: x.decode("utf-8", errors="ignore")
)

print("Backstory files:")
backstory_df["file_name"].tolist()


Backstory files:


[pw.Json('train.csv'), pw.Json('test.csv')]

In [12]:
def parse_csv_files(df):
    parsed = {}
    for _, row in df.iterrows():
        file_name = str(row["file_name"])   # <-- FIX
        csv_df = pd.read_csv(io.StringIO(row["content"]))
        parsed[file_name] = csv_df
    return parsed


csv_data = parse_csv_files(backstory_df)

for name, df in csv_data.items():
    clean_name = str(name).replace('"', "").replace("'", "")  # <-- SAFE
    out_name = f"processed_{clean_name}"
    df.to_csv(out_name, index=False)
    print(f"Saved {out_name}")


Saved processed_train.csv
Saved processed_test.csv


In [14]:
!ls


 credentials.json			 processed_test.csv
'local_In search of the castaways.txt'	 processed_train.csv
'local_The Count of Monte Cristo.txt'	 sample_data


In [15]:
from google.colab import files

for f in os.listdir():
    if f.startswith("local_") or f.startswith("processed_"):
        files.download(f)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>